# Data Parallel in Spark

- Download [Movie Dataset](https://www.cs.wcupa.edu/lngo/data/ml-latest.zip)
- Unzip the movie data file.

In [1]:
import os
import sys

spark_path = os.environ['SPARK_HOME']
sys.path.append(spark_path + "/bin")
sys.path.append(spark_path + "/python")
sys.path.append(spark_path + "/python/pyspark/")
sys.path.append(spark_path + "/python/lib")
sys.path.append(spark_path + "/python/lib/pyspark.zip")
sys.path.append(spark_path + "/python/lib/py4j-0.10.9-src.zip")

import findspark
findspark.init()

import pyspark

In [2]:
number_cores = 8
memory_gb = 12
conf = (pyspark.SparkConf().
        setMaster('local[{}]'.format(number_cores)).
        set('spark.driver.memory', '{}g'.format(memory_gb)))
sc = pyspark.SparkContext(conf=conf)

In [3]:
# You need to provide either an absolute or relative path to your data location here. 
# This notation is for Windows DOS commands
!dir e:\data\ml-latest\

 Volume in drive E is WAREHOUSE
 Volume Serial Number is 6077-E9E2

 Directory of e:\data\ml-latest

09/11/2022  10:25 PM    <DIR>          .
09/11/2022  10:24 PM    <DIR>          ..
09/26/2018  05:44 PM       414,851,573 genome-scores.csv
09/26/2018  05:44 PM            18,103 genome-tags.csv
09/26/2018  05:37 PM         1,267,039 links.csv
09/26/2018  05:35 PM         2,858,223 movies.csv
09/26/2018  05:31 PM       759,200,511 ratings.csv
09/26/2018  05:46 PM             9,784 README.txt
09/26/2018  05:11 PM        39,744,990 tags.csv
               7 File(s)  1,217,950,223 bytes
               2 Dir(s)  1,106,383,896,576 bytes free


In [4]:
ratings = sc.textFile("e:/data/ml-latest/ratings.csv")

In [6]:
ratings.take(5)

['userId,movieId,rating,timestamp',
 '1,307,3.5,1256677221',
 '1,481,3.5,1256677456',
 '1,1091,1.5,1256677471',
 '1,1257,4.5,1256677460']

The `cache` function tells Spark to keep the data in memory (after an action has been invoked)

In [7]:
ratings.cache()

e:/data/ml-latest/ratings.csv MapPartitionsRDD[1] at textFile at NativeMethodAccessorImpl.java:0

In [8]:
%%time
ratings.count()

Wall time: 20.4 s


27753445

In [9]:
%%time
ratings.count()

Wall time: 18.2 s


27753445

In [10]:
%%time
ratings.count()

Wall time: 17.6 s


27753445

## Average ratings 

- Finding the average ratings over the years of each individual movies
- Procedural: 
  - For each movie 
    - add together all rating values, 
    - count all rating entries
    - divide sum of rating values by count of rating entries
- Data flow:
  - Backtracking from the result:
    - Individual average ratings of all movies
    - Average rating of one movie
    - Collections of all ratings for that movie
      - Sum
      - Count
    - List of all ratings

In [11]:
ratingHeader = ratings.first()
print(ratingHeader)

userId,movieId,rating,timestamp


In [12]:
ratingsOnly = ratings.filter(lambda x: x != ratingHeader)
ratingsOnly.take(5)

['1,307,3.5,1256677221',
 '1,481,3.5,1256677456',
 '1,1091,1.5,1256677471',
 '1,1257,4.5,1256677460',
 '1,1449,4.5,1256677264']

In [13]:
s = '1,307,3.5,1256677221'
s.split(",")[2]

'3.5'

In [14]:
movieRatings = ratingsOnly.map(lambda line: (line.split(",")[1], float(line.split(",")[2])))
movieRatings.take(5)

[('307', 3.5), ('481', 3.5), ('1091', 1.5), ('1257', 4.5), ('1449', 4.5)]

## Possible approaches in aggregating data

- `groupByKey` and `mapValues`
- `reduceByKey` and `countByKey`

*groupByKey* and *mapValues*

In [15]:
groupByKeyRatings = movieRatings.groupByKey()
groupByKeyRatings.take(5)

[('3826', <pyspark.resultiterable.ResultIterable at 0x24ed82cdef0>),
 ('104', <pyspark.resultiterable.ResultIterable at 0x24ed82cd438>),
 ('153', <pyspark.resultiterable.ResultIterable at 0x24ed82cdf98>),
 ('165', <pyspark.resultiterable.ResultIterable at 0x24ed82cd208>),
 ('181', <pyspark.resultiterable.ResultIterable at 0x24ed82ed7f0>)]

In [16]:
mapValuesToListRatings = groupByKeyRatings.mapValues(list)
mapValuesToListRatings.take(5)

[('3826',
  [2.0,
   3.0,
   3.0,
   3.0,
   4.0,
   3.0,
   1.0,
   3.0,
   3.0,
   1.0,
   2.0,
   2.0,
   3.0,
   2.0,
   3.0,
   3.0,
   2.0,
   2.0,
   2.0,
   0.5,
   3.0,
   3.0,
   1.0,
   1.5,
   2.0,
   4.0,
   2.0,
   3.0,
   1.0,
   4.0,
   3.5,
   2.0,
   2.5,
   2.0,
   3.5,
   2.0,
   2.5,
   2.0,
   3.5,
   3.0,
   0.5,
   1.5,
   1.5,
   1.0,
   1.0,
   2.5,
   1.5,
   1.0,
   4.0,
   0.5,
   2.0,
   2.5,
   3.5,
   2.0,
   0.5,
   1.0,
   2.0,
   2.0,
   2.0,
   2.5,
   2.0,
   2.0,
   3.0,
   3.0,
   3.5,
   3.5,
   2.0,
   3.0,
   0.5,
   2.0,
   1.0,
   2.0,
   2.5,
   2.5,
   1.0,
   1.5,
   3.0,
   3.0,
   3.0,
   2.0,
   2.5,
   3.0,
   3.5,
   2.0,
   4.0,
   0.5,
   4.0,
   2.5,
   3.0,
   4.5,
   4.0,
   2.5,
   2.0,
   3.0,
   2.5,
   3.0,
   2.5,
   2.0,
   2.5,
   2.0,
   2.0,
   2.0,
   5.0,
   4.0,
   3.0,
   2.0,
   1.0,
   3.0,
   2.5,
   1.0,
   1.5,
   2.5,
   1.5,
   1.0,
   3.0,
   3.0,
   4.0,
   3.0,
   3.0,
   3.0,
   2.5,
   4.5,
   2.5,
   3.0

In [17]:
avgRatings01 = mapValuesToListRatings.mapValues(lambda V: sum(V) / float(len(V)))
avgRatings01.take(10)

[('3826', 2.5461339626882444),
 ('104', 3.3942778801636178),
 ('153', 2.9020622558025204),
 ('165', 3.5077587042963825),
 ('181', 1.9860046651116294),
 ('253', 3.5052233084147977),
 ('423', 3.008343508343508),
 ('494', 3.3739313292884723),
 ('762', 2.414987080103359),
 ('1396', 3.6338256484149856)]

In [18]:
test = [2.0, 4.0, 3.0]
sum(test) / len(test)

3.0

*reduceByKey* and *countByKey*

In [19]:
countsByKey = movieRatings.countByKey()
countsByKey

defaultdict(int,
            {'307': 7958,
             '481': 6037,
             '1091': 6138,
             '1257': 5902,
             '1449': 6867,
             '1590': 8511,
             '1591': 6508,
             '2134': 7020,
             '2478': 7797,
             '2840': 6047,
             '2986': 6060,
             '3020': 7783,
             '3424': 7265,
             '3698': 8269,
             '3826': 8898,
             '3893': 5259,
             '170': 9574,
             '849': 9878,
             '1186': 8643,
             '1235': 9937,
             '1244': 10249,
             '1296': 7470,
             '1663': 9581,
             '1962': 10219,
             '2108': 7729,
             '2243': 6398,
             '2352': 7517,
             '2707': 8198,
             '2746': 10142,
             '2915': 9590,
             '3363': 9001,
             '640': 3393,
             '828': 1736,
             '960': 173,
             '1221': 38875,
             '1321': 9175,
             '1

In [20]:
def sumValues(x, y):
    return (x + y)

In [21]:
sumRatings = movieRatings.reduceByKey(sumValues)
sumRatings.take(5)

[('3826', 22655.5),
 ('104', 75512.5),
 ('153', 112156.0),
 ('165', 144674.0),
 ('181', 5960.0)]

In [22]:
avgRatings02 = sumRatings.map(lambda x: (x[0], x[1]/countsByKey.get(x[0])))
avgRatings02.take(10)

[('3826', 2.5461339626882444),
 ('104', 3.3942778801636178),
 ('153', 2.9020622558025204),
 ('165', 3.5077587042963825),
 ('181', 1.9860046651116294),
 ('253', 3.5052233084147977),
 ('423', 3.008343508343508),
 ('494', 3.3739313292884723),
 ('762', 2.414987080103359),
 ('1396', 3.6338256484149856)]

In [23]:
movies = sc.textFile("e:/data/ml-latest/movies.csv")
movies.take(5)

['movieId,title,genres',
 '1,Toy Story (1995),Adventure|Animation|Children|Comedy|Fantasy',
 '2,Jumanji (1995),Adventure|Children|Fantasy',
 '3,Grumpier Old Men (1995),Comedy|Romance',
 '4,Waiting to Exhale (1995),Comedy|Drama|Romance']

In [24]:
movieHeader = movies.first()
movieInfo = movies.filter(lambda x: x != movieHeader)
movieInfo.take(100)

['1,Toy Story (1995),Adventure|Animation|Children|Comedy|Fantasy',
 '2,Jumanji (1995),Adventure|Children|Fantasy',
 '3,Grumpier Old Men (1995),Comedy|Romance',
 '4,Waiting to Exhale (1995),Comedy|Drama|Romance',
 '5,Father of the Bride Part II (1995),Comedy',
 '6,Heat (1995),Action|Crime|Thriller',
 '7,Sabrina (1995),Comedy|Romance',
 '8,Tom and Huck (1995),Adventure|Children',
 '9,Sudden Death (1995),Action',
 '10,GoldenEye (1995),Action|Adventure|Thriller',
 '11,"American President, The (1995)",Comedy|Drama|Romance',
 '12,Dracula: Dead and Loving It (1995),Comedy|Horror',
 '13,Balto (1995),Adventure|Animation|Children',
 '14,Nixon (1995),Drama',
 '15,Cutthroat Island (1995),Action|Adventure|Romance',
 '16,Casino (1995),Crime|Drama',
 '17,Sense and Sensibility (1995),Drama|Romance',
 '18,Four Rooms (1995),Comedy',
 '19,Ace Ventura: When Nature Calls (1995),Comedy',
 '20,Money Train (1995),Action|Comedy|Crime|Drama|Thriller',
 '21,Get Shorty (1995),Comedy|Crime|Thriller',
 '22,Copycat 

In [25]:
movieTitles = movieInfo.map(lambda line: (line.split(",",1)[0], line.rsplit(",",1)[0].split(",",1)[1]))
movieTitles.take(20)

[('1', 'Toy Story (1995)'),
 ('2', 'Jumanji (1995)'),
 ('3', 'Grumpier Old Men (1995)'),
 ('4', 'Waiting to Exhale (1995)'),
 ('5', 'Father of the Bride Part II (1995)'),
 ('6', 'Heat (1995)'),
 ('7', 'Sabrina (1995)'),
 ('8', 'Tom and Huck (1995)'),
 ('9', 'Sudden Death (1995)'),
 ('10', 'GoldenEye (1995)'),
 ('11', '"American President, The (1995)"'),
 ('12', 'Dracula: Dead and Loving It (1995)'),
 ('13', 'Balto (1995)'),
 ('14', 'Nixon (1995)'),
 ('15', 'Cutthroat Island (1995)'),
 ('16', 'Casino (1995)'),
 ('17', 'Sense and Sensibility (1995)'),
 ('18', 'Four Rooms (1995)'),
 ('19', 'Ace Ventura: When Nature Calls (1995)'),
 ('20', 'Money Train (1995)'),
 ('21', 'Get Shorty (1995)'),
 ('22', 'Copycat (1995)'),
 ('23', 'Assassins (1995)'),
 ('24', 'Powder (1995)'),
 ('25', 'Leaving Las Vegas (1995)'),
 ('26', 'Othello (1995)'),
 ('27', 'Now and Then (1995)'),
 ('28', 'Persuasion (1995)'),
 ('29', '"City of Lost Children, The (Cité des enfants perdus, La) (1995)"'),
 ('30', 'Shanghai

In [26]:
s = '29,"City of Lost Children, The (Cité des enfants perdus, La) (1995)",Adventure|Drama|Fantasy|Mystery|Sci-Fi'
print(s.split(","))
print(s.rsplit(",",1)[0])
print(s.rsplit(",",1)[0].split(",",1)[1])

['29', '"City of Lost Children', ' The (Cité des enfants perdus', ' La) (1995)"', 'Adventure|Drama|Fantasy|Mystery|Sci-Fi']
29,"City of Lost Children, The (Cité des enfants perdus, La) (1995)"
"City of Lost Children, The (Cité des enfants perdus, La) (1995)"


In [27]:
augmentedRatings = avgRatings01.join(movieTitles)
augmentedRatings.take(10)

[('854',
  (3.722689075630252, '"Ballad of Narayama, The (Narayama Bushiko) (1958)"')),
 ('8591', (3.1783018867924526, '"Philadelphia Experiment, The (1984)"')),
 ('5902', (3.833290751149719, 'Adaptation (2002)')),
 ('1938', (3.859350237717908, '"Lost Weekend, The (1945)"')),
 ('2099', (3.5872438863185723, 'Song of the South (1946)')),
 ('2713', (2.5252918287937742, 'Lake Placid (1999)')),
 ('5833', (3.3345864661654137, 'Dog Soldiers (2002)')),
 ('4899', (2.359262229350441, 'Black Knight (2001)')),
 ('509', (3.6844782352626226, '"Piano, The (1993)"')),
 ('106022', (3.402390438247012, 'Toy Story of Terror (2013)'))]

In [28]:
augmentedRatings.takeOrdered(50, key = lambda x: -x[1][0])

[('134633', (5.0, 'Tony 10 (2012)')),
 ('156307', (5.0, 'Pardon My Sarong (1942)')),
 ('92783', (5.0, 'Latin Music USA (2009)')),
 ('161468', (5.0, 'Nutcracker Fantasy (1979)')),
 ('136872', (5.0, 'Zapatlela (1993)')),
 ('183261', (5.0, 'Sexting in Suburbia (2012)')),
 ('165787', (5.0, 'Lonesome Dove Church (2014)')),
 ('158370', (5.0, 'Muzungu (1999)')),
 ('185637', (5.0, 'Crítico (2008)')),
 ('184151', (5.0, 'VeggieTales: Celery Night Fever (2014)')),
 ('134757', (5.0, 'The Last Hunt (1956)')),
 ('124174', (5.0, 'Until They Sail (1957)')),
 ('182453', (5.0, 'Pure Fucking Mayhem (2008)')),
 ('137980', (5.0, "The Fall of '55 (2006)")),
 ('129478', (5.0, 'A Blank on the Map (1971)')),
 ('160624', (5.0, 'Big Man - An Unusual Insurance (1988)')),
 ('130558', (5.0, 'Shark Kill (1976)')),
 ('159125', (5.0, "Anybody's Son Will Do")),
 ('187793', (5.0, 'The Bride (1973)')),
 ('136992', (5.0, "When He Didn't Come Home (1998)")),
 ('179183', (5.0, 'Dragon Lee Vs. The 5 Brothers (1978)')),
 ('11

## Challenge 1:

Report the average ratings for movies with ratings higher than 3.75 and the number of ratings total at least 1000. 

## Challenge 2:

Study the genome tags and answer the following question. 
How do user perceive and distinguish sub-genres? For example, what is the difference between `action` and `action comedy`? 